# 模型和预训练权重

{mod}`torchvision.models` 子包包含用于解决不同任务的模型定义，包括：图像分类、像素级语义分割、目标检测、实例分割、人体关键点检测、视频分类和光流。

参考：[models](https://pytorch.org/vision/stable/models.html)

## 关于预训练权重的一般信息
TorchVision 为每个提供的架构提供了使用 PyTorch torch.hub 的预训练权重。实例化预训练模型将下载其权重到缓存目录。可以使用 `TORCH_HOME` 环境变量设置此目录。有关详细信息，请参阅 {func}`torch.hub.load_state_dict_from_url`。

## 初始化预训练模型

截至 v0.13，TorchVision 为现有模型构建方法提供了新的 [多权重支持 API](https://pytorch.org/blog/introducing-torchvision-new-multi-weight-support-api/) 来加载不同的权重：

In [2]:
from torchvision.models import resnet50, ResNet50_Weights

# Old weights with accuracy 76.130%
resnet50(weights=ResNet50_Weights.IMAGENET1K_V1)

# New weights with accuracy 80.858%
resnet50(weights=ResNet50_Weights.IMAGENET1K_V2)

# Best available weights (currently alias for IMAGENET1K_V2)
# Note that these weights may change across versions
resnet50(weights=ResNet50_Weights.DEFAULT)

# Strings are also supported
resnet50(weights="IMAGENET1K_V2")

# No weights - random initialization
resnet50(weights=None);

迁移到新的 API 非常简单。以下两个 API 之间的方法调用是等效的：

In [4]:
from torchvision.models import resnet50, ResNet50_Weights

# Using pretrained weights:
resnet50(weights=ResNet50_Weights.IMAGENET1K_V1)
resnet50(weights="IMAGENET1K_V1")
resnet50(pretrained=True)  # deprecated
resnet50(True)  # deprecated

# Using no weights:
resnet50(weights=None)
resnet50()
resnet50(pretrained=False)  # deprecated
resnet50(False);  # deprecated

## 使用预训练模型
在使用预训练模型之前，必须对图像进行预处理（使用正确的分辨率/插值调整大小，应用推理转换，重新缩放值等）。由于这取决于给定模型的训练方式，因此没有标准的方法。它可以在不同的模型族、变体甚至权重版本之间有所不同。使用正确的预处理方法至关重要，否则可能导致准确性下降或输出错误。

每个预训练模型的推理转换所需的所有信息都在其权重文档中提供。为了简化推理，TorchVision 将必要的预处理转换捆绑到每个模型权重中。这些可以通过 `weight.transforms` 属性访问：

```python
# Initialize the Weight Transforms
weights = ResNet50_Weights.DEFAULT
preprocess = weights.transforms()

# Apply it to the input image
img_transformed = preprocess(img)
```

一些模型使用具有不同训练和评估行为的模块，例如批量归一化。要在这些模式之间切换，请使用 `model.train()` 或 `model.eval()`（视情况而定）。有关详细信息，请参阅 [`train`](https://pytorch.org/docs/stable/generated/torch.nn.Module.html#torch.nn.Module.train) 或 [`eval`](https://pytorch.org/docs/stable/generated/torch.nn.Module.html#torch.nn.Module.eval)。

```python
# Initialize model
weights = ResNet50_Weights.DEFAULT
model = resnet50(weights=weights)

# Set model to eval mode
model.eval()
```

## 列出和检索可用的模型

从v0.14开始，TorchVision 提供了一种新的机制，允许通过名称列出和检索模型和权重。以下是一些使用示例：

```python
# List available models
all_models = list_models()
classification_models = list_models(module=torchvision.models)

# Initialize models
m1 = get_model("mobilenet_v3_large", weights=None)
m2 = get_model("quantized_mobilenet_v3_large", weights="DEFAULT")

# Fetch weights
weights = get_weight("MobileNet_V3_Large_QuantizedWeights.DEFAULT")
assert weights == MobileNet_V3_Large_QuantizedWeights.DEFAULT

weights_enum = get_model_weights("quantized_mobilenet_v3_large")
assert weights_enum == MobileNet_V3_Large_QuantizedWeights

weights_enum2 = get_model_weights(torchvision.models.quantization.mobilenet_v3_large)
assert weights_enum == weights_enum2
```

## 使用来自 Hub 的模型

大多数预训练模型可以通过 PyTorch Hub 直接访问，而无需安装 TorchVision：

In [7]:
import torch

# Option 1: passing weights param as string
model = torch.hub.load("pytorch/vision", "resnet50", weights="IMAGENET1K_V2")

# Option 2: passing weights param as enum
weights = torch.hub.load("pytorch/vision", "get_weight", weights="ResNet50_Weights.IMAGENET1K_V2")
model = torch.hub.load("pytorch/vision", "resnet50", weights=weights)

Downloading: "https://github.com/pytorch/vision/zipball/main" to /home/ai/.cache/torch/hub/main.zip


RemoteDisconnected: Remote end closed connection without response

您还可以通过执行以下操作来检索特定模型的所有可用权重：

In [ ]:
import torch

weight_enum = torch.hub.load("pytorch/vision", "get_model_weights", name="resnet50")
print([weight for weight in weight_enum])